In [5]:
import os
import json
import pandas as pd
import traceback


ModuleNotFoundError: No module named 'pandas'

In [6]:
from langchain_openai import ChatOpenAI


In [7]:
import os
key=os.getenv('OPEN_API_KEY')

In [9]:
from dotenv import load_dotenv
load_dotenv()

True

In [12]:
llm = ChatOpenAI(
    openai_api_key=key,  # ✅ correct argument name
    model="gpt-4o-mini",
    temperature=0.5
)

In [13]:
llm

ChatOpenAI(client=<openai.resources.chat.completions.completions.Completions object at 0x000001C26A9A8AD0>, async_client=<openai.resources.chat.completions.completions.AsyncCompletions object at 0x000001C26A9A9550>, root_client=<openai.OpenAI object at 0x000001C26A5BFED0>, root_async_client=<openai.AsyncOpenAI object at 0x000001C26A9A92B0>, model_name='gpt-4o-mini', temperature=0.5, model_kwargs={}, openai_api_key=SecretStr('**********'))

In [18]:
from langchain_openai import OpenAI
from langchain.prompts import PromptTemplate
from langchain.chains import LLMChain, SequentialChain
from langchain.callbacks import get_openai_callback
import PyPDF2


In [140]:
TEMPLATE="""
Text:{text}

you are an expert MCqs maker, given the above text. It is your job to create a quiz of {numbers},
 multiple quiz-wise questions for {subject}, students in {tone} tone. In curly brackets,
   make sure the questions are not repeated and check all the questions to be confirming the text as well.
     Make sure to format your response like response.json below and use it as a guide. Make sure to make dash {numbers} of MCqs
     
# response.json.
{response_json}"""

In [141]:
quiz_generation_prompt=PromptTemplate(
    input_variable=['text','number','subject','tone','response.json'],
    template=TEMPLATE
)

In [142]:
RESPONSE_JSON={
    "1":{
        'mcq':'multiple choice question',
        'option': {
            'a':'choice here',
            'b' :'choice here',
            'c':'choice here',
            'd':  'choice here'            
    },
    'correct':'correct answer',
    },
   "2":{
        'mcq':'multiple choice question',
        'option': {
            'a':'choice here',
            'b' :'choice here',
            'c':'choice here',
            'd':  'choice here'            
    },
    'correct':'correct answer'
    },
"3":{
        'mcq':'multiple choice question',
        'option': {
            'a':'choice here',
            'b' :'choice here',
            'c':'choice here',
            'd':  'choice here'            
    },
    'correct':'correct answer',
    },
    "4":{
        'mcq':'multiple choice question',
        'option': {
            'a':'choice here',
            'b' :'choice here',
            'c':'choice here',
            'd':  'choice here'            
    },
    'correct':'correct answer',
    },

},


In [143]:
# chain
quiz_chain=LLMChain(llm=llm,
                    prompt=quiz_generation_prompt,
                    output_key='quiz',verbose=True)

In [144]:
TEMPLATE2="""
You are an expert teacher .given a multiple choice quiz for {subject} students.
You need to evalute the complexity of the question and give a complete analysis of the quiz .only use 50 words for complexity 
if the quiz is not per with the congitive and analytical abilities of the student.
Update the quiz questions which needs to be changed and change the tone such that is perfectly fits the student level.
Check the quiz answer realted to the content .
Quiz_MCQS
{quiz}

"""

In [145]:
quiz_generation_prompt=PromptTemplate(
    input_variable=['subject','quiz'],
    template=TEMPLATE2
)

In [146]:
# chain2
review_chain=LLMChain(llm=llm,prompt=quiz_generation_prompt,
                      output_key='review',
                      verbose=True
                      )

In [160]:

generate_chains = SequentialChain(
    chains=[quiz_chain, review_chain], 
    input_variables=['text', 'numbers', 'subject', 'tone', 'response_json'],  # ✅ cleaned
    output_variables=["quiz", "review"],                                     # ✅ matches invoke
    verbose=True
)





In [ ]:
file_path = r"C:\Users\user\mcqgen\experiment\data.txt"  # raw string prevents \ issues
with open(file_path, 'r', encoding='utf-8') as file:     # encoding avoids Unicode errors
    Text = file.read()

 # preview first 200 characters


In [148]:
print(full_text)

Artiﬁcial Intelligence
A Modern Approach
Third Edition
PRENTICE HALL SERIES
IN ARTIFICIAL INTELLIGENCE
Stuart Russell and Peter Norvig, Editors
FORSYTH &P ONCE Computer Vision: A Modern Approach
GRAHAM ANSI Common Lisp
JURAFSKY &M ARTIN Speech and Language Processing, 2nd ed.
NEAPOLITAN Learning Bayesian Networks
RUSSELL &N ORVIG Artiﬁcial Intelligence: A Modern Approach, 3rd ed.
Artiﬁcial Intelligence
A Modern Approach
Third Edition
Stuart J. Russell and Peter Norvig
Contributing writers :
Ernest Davis
Douglas D. Edwards
David Forsyth
Nicholas J. Hay
Jitendra M. Malik
Vibhu Mittal
Mehran Sahami
Sebastian Thrun
Upper Saddle River Boston Columbus San Francisco New York
Indianapolis London Toronto Sydney Singapore Tokyo Montreal
Dubai Madrid Hong Kong Mexico City Munich Paris Amsterdam Cape Town
Vice President and Editorial Director, ECS: Marcia J. Horton
Editor-in-Chief: Michael Hirsch
Executive Editor: Tracy Dunkelberger
Assistant Editor: Melinda Haggerty
Editorial Assistant: Allison M

In [154]:
#convert python dict into json formatted
quiz=json.dumps(RESPONSE_JSON)

In [155]:
quiz

'[{"1": {"mcq": "multiple choice question", "option": {"a": "choice here", "b": "choice here", "c": "choice here", "d": "choice here"}, "correct": "correct answer"}, "2": {"mcq": "multiple choice question", "option": {"a": "choice here", "b": "choice here", "c": "choice here", "d": "choice here"}, "correct": "correct answer"}, "3": {"mcq": "multiple choice question", "option": {"a": "choice here", "b": "choice here", "c": "choice here", "d": "choice here"}, "correct": "correct answer"}, "4": {"mcq": "multiple choice question", "option": {"a": "choice here", "b": "choice here", "c": "choice here", "d": "choice here"}, "correct": "correct answer"}}]'

In [156]:
extracted_text = extract_pdf_text(file_path)

Artiﬁcial Intelligence
A Modern Approach
Third Edition
PRENTICE HALL SERIES
IN ARTIFICIAL INTELLIGEN


In [158]:
# Define chain inputs
numbers = 5                # how many MCQs you want (use singular, not numbers)
subject = "Artifical Intelligence"        # or any subject you need
tone = "student-friendly"  # style of the quiz
RESPONSE_JSON = {
    "quiz": [],
    "review": ""
}


In [159]:
with get_openai_callback() as cb:
    response = generate_chains.invoke(
        {
            "text": extracted_text,             # ✅ matches chain input
            "numbers": numbers,                  # ✅ singular, not "numbers"
            "subject": subject,
            "tone": tone,
            "response_json": json.dumps(RESPONSE_JSON),
           

        }
    )





> Entering new SequentialChain chain...


> Entering new LLMChain chain...
Prompt after formatting:

Text:Artiﬁcial Intelligence
A Modern Approach
Third Edition
PRENTICE HALL SERIES
IN ARTIFICIAL INTELLIGENCE
Stuart Russell and Peter Norvig, Editors
FORSYTH &P ONCE Computer Vision: A Modern Approach
GRAHAM ANSI Common Lisp
JURAFSKY &M ARTIN Speech and Language Processing, 2nd ed.
NEAPOLITAN Learning Bayesian Networks
RUSSELL &N ORVIG Artiﬁcial Intelligence: A Modern Approach, 3rd ed.
Artiﬁcial Intelligence
A Modern Approach
Third Edition
Stuart J. Russell and Peter Norvig
Contributing writers :
Ernest Davis
Douglas D. Edwards
David Forsyth
Nicholas J. Hay
Jitendra M. Malik
Vibhu Mittal
Mehran Sahami
Sebastian Thrun
Upper Saddle River Boston Columbus San Francisco New York
Indianapolis London Toronto Sydney Singapore Tokyo Montreal
Dubai Madrid Hong Kong Mexico City Munich Paris Amsterdam Cape Town
Vice President and Editorial Director, ECS: Marcia J. Horton
Editor-in-Chief: Michael H

RateLimitError: Error code: 429 - {'error': {'message': 'Request too large for gpt-4o-mini in organization org-pmqOGHmZZcZRtpGLtGVBJ8bL on tokens per min (TPM): Limit 60000, Requested 877881. The input or output tokens must be reduced in order to run successfully. Visit https://platform.openai.com/account/rate-limits to learn more. You can increase your rate limit by adding a payment method to your account at https://platform.openai.com/account/billing.', 'type': 'tokens', 'param': None, 'code': 'rate_limit_exceeded'}}